In [1]:
from __future__ import absolute_import, division, print_function

import wandb
import base64
import imageio
import IPython
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
import PIL.Image
import pyvirtualdisplay
import random
import pprint

import tensorflow as tf
from tensorflow import concat
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dropout, Input, Flatten, Dense, Concatenate
from tensorflow.keras.losses import CategoricalCrossentropy, Huber, MeanSquaredError
from tensorflow.keras.metrics import categorical_accuracy
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.regularizers import l2
from tensorflow import reshape


from tf_agents.agents.dqn import dqn_agent
from tf_agents.drivers import py_driver
from tf_agents.environments import py_environment
from tf_agents.environments import utils
from tf_agents.environments import tf_py_environment
from tf_agents.eval import metric_utils
from tf_agents.metrics import tf_metrics
from tf_agents.networks import sequential
from tf_agents.policies import py_tf_eager_policy
from tf_agents.policies import random_tf_policy
from tf_agents.replay_buffers import reverb_replay_buffer
from tf_agents.replay_buffers import reverb_utils
from tf_agents.trajectories import trajectory
from tf_agents.trajectories import time_step as ts
from tf_agents.specs import array_spec, tensor_spec
from tf_agents.utils import common

from spektral.layers import XENetDenseConv
from spektral.transforms import LayerPreprocess
from spektral.utils.sparse import sp_matrix_to_sp_tensor
from spektral.data import Graph
from spektral.data.dataset import Dataset
from spektral.data.loaders import BatchLoader

from wandb.keras import WandbCallback

from collections import deque
from random import sample

2022-06-15 18:08:35.662442: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-06-15 18:08:35.662480: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [2]:
sweep_config = {
    "name": 'v2 - 1st Run',
    'method':'bayes'
}

metric = {
    'name' : 'loss',
    'goal' : 'minimize'
}
sweep_config['metric'] = metric


parameters_dict = {
    'N_xenet': {
        'distribution': 'int_uniform',
        'min': 1,
        'max': 3
    },
    'N_dense': {
        'distribution': 'int_uniform',
        'min': 0,
        'max': 5
    },
    'division_factor_dense': {
        'value': 1
    },
    'p_drop': {
        'value': 0
    },
    'stack_channels': {
        'distribution': 'int_uniform',
        'min': 5,
        'max': 200
    },
    'node_channels': {
        'distribution': 'int_uniform',
        'min': 5,
        'max': 200
    },
    'edge_channels': {
        'distribution': 'int_uniform',
        'min': 5,
        'max': 200
    },
    'train_episodes': {
        'distribution': 'int_uniform',
        'min': 50,
        'max': 150
    },    
    'MIN_REPLAY_SIZE': {
        'value': 200
    },
    'batch_size': {
        'distribution': 'int_uniform',
        'min': 10,
        'max': 200
    },
    'step_buffer': {
        'value': 8
    },
    'step_buffer_set': {
        'distribution': 'int_uniform',
        'min': 5,
        'max': 8
    },
    'set_target': {
        'distribution': 'int_uniform',
        'min': 3,
        'max': 50
    },
    'decay' : {
        'distribution': 'uniform',
        'min': 0.0001,
        'max': 0.1
    },
    'discount_factor' : {
        'distribution': 'uniform',
        'min': 0.1,
        'max': 0.9
    },
    'lr' : {
        'distribution': 'uniform',
        'min': 0.0001,
        'max': 0.01
    }
}
sweep_config['parameters'] = parameters_dict

pprint.pprint(sweep_config)

{'method': 'bayes',
 'metric': {'goal': 'minimize', 'name': 'loss'},
 'name': 'v2 - 1st Run',
 'parameters': {'MIN_REPLAY_SIZE': {'value': 200},
                'N_dense': {'distribution': 'int_uniform', 'max': 5, 'min': 0},
                'N_xenet': {'distribution': 'int_uniform', 'max': 3, 'min': 1},
                'batch_size': {'distribution': 'int_uniform',
                               'max': 200,
                               'min': 10},
                'decay': {'distribution': 'uniform', 'max': 0.1, 'min': 0.0001},
                'discount_factor': {'distribution': 'uniform',
                                    'max': 0.9,
                                    'min': 0.1},
                'division_factor_dense': {'value': 1},
                'edge_channels': {'distribution': 'int_uniform',
                                  'max': 200,
                                  'min': 5},
                'lr': {'distribution': 'uniform', 'max': 0.01, 'min': 0.0001},
                

In [3]:
sweep_id = wandb.sweep(sweep_config, project="BayesSearch - D=2 & L=5", entity="locp")

Create sweep with ID: jl3vo8s3
Sweep URL: https://wandb.ai/locp/BayesSearch%20-%20D%3D2%20%26%20L%3D5/sweeps/jl3vo8s3


parametri
- number of train_episodes
- size of replay_memory
- update steps of main and target network
- learning_rate
- discount_factor
- MIN_REPLAY_SIZE (minimum size of the replay_memory for which we do the training)
- batch_size

## Environment

### Predefined Functions 

##### Sparse Matrix Creation

In [4]:
def sparseAdj(D, L):
    N = L**D
    nodes = [x for x in np.ndindex(tuple(np.repeat(L,D)))]
    mul = [L**i for i in reversed(range(D))]

    A_dense = []
    for node in nodes:
        temp_buffer = []
        A_dense_row = [0]*N
        for d in range(D):
            temp=list(node)
            temp[d]=((temp[d]+1)%L)
            temp=np.inner(temp, mul)
            temp_buffer.append(temp)    

            temp=list(node)
            temp[d]=((temp[d]-1)%L)
            temp=np.inner(temp, mul)
            temp_buffer.append(temp)
      
        temp_buffer=list(np.unique(np.array(temp_buffer), axis=0))   
        for i in temp_buffer: A_dense_row[i]=1
        A_dense.append(A_dense_row)

    return sp_matrix_to_sp_tensor(np.array(A_dense))

In [5]:
def denseAdj(D, L):
    N = L**D
    nodes = [x for x in np.ndindex(tuple(np.repeat(L,D)))]
    mul = [L**i for i in reversed(range(D))]

    A_dense = []
    for node in nodes:
        temp_buffer = []
        A_dense_row = [0]*N
        for d in range(D):
            temp=list(node)
            temp[d]=((temp[d]+1)%L)
            temp=np.inner(temp, mul)
            temp_buffer.append(temp)    

            temp=list(node)
            temp[d]=((temp[d]-1)%L)
            temp=np.inner(temp, mul)
            temp_buffer.append(temp)
      
        temp_buffer=list(np.unique(np.array(temp_buffer), axis=0))   
        for i in temp_buffer: A_dense_row[i]=1
        A_dense.append(A_dense_row)

    return np.array(A_dense)

In [6]:
def J_inter(denseAdj):
    N = denseAdj.shape[0]
    sparseAdj = sp_matrix_to_sp_tensor(denseAdj)
    edge=sparseAdj.indices.numpy()
    un_edge=np.array([np.sort(i) for i in edge]) 
    inter=[]
    for i in range(len(un_edge)):
        equal=True
        for j in range(i):
            if np.array_equal(un_edge[i],un_edge[j]):
                inter.append(inter[j])
                equal=False
                break
        if equal: 
            inter.append(np.random.normal(0, 1))
    
    inter_matrix = np.zeros((N,N))
    counter = 0
    for i, j in edge:
        inter_matrix[i,j] = inter[counter]
        counter += 1
    return [np.array(inter).reshape(sparseAdj.indices.shape[0],1), inter_matrix.reshape((N,N,1))]

    # 0 => interaction array
    # 1 => interaction matrix (zero padded)

In [7]:
class SG_env(py_environment.PyEnvironment):

  def __init__(self, L, D):
    
    self.N = L**D
    self._action_spec = array_spec.BoundedArraySpec(
        shape=(), dtype=np.int32, minimum=0, maximum=self.N-1, name='action')
    self._observation_spec = array_spec.BoundedArraySpec(
        shape=(self.N,1), dtype=np.int32, minimum=-1, maximum=1, name='observation')
    self.sp_AdjMat = sparseAdj(D=D, L=L)
    self.dense_AdjMat = denseAdj(D=D, L=L)
    self.Jlist = J_inter(self.dense_AdjMat)
    self.interaction = self.Jlist[0]   
    self.inter_matrix = self.Jlist[1]
    self._state = np.ones(shape=(self.N,1)).astype("int32")
    self._episode_ended = False

  def get_state(self):
    return self._state

  def show_N(self):
    return self.N  

  def action_spec(self):
    return self._action_spec

  def observation_spec(self):
    return self._observation_spec

  def show_dense_AdjMat(self):
    return self.dense_AdjMat

  def show_sp_AdjMat(self):
    return self.sp_AdjMat

  def show_interaction(self):
    return self.interaction

  def show_inter_matrix(self):
    return self.inter_matrix

  def __all_spins_down(self):
    return np.all(self._state==-1)    # True => All spins = -1, False otherwise

  def computeReward(self, action):
    nns = self.sp_AdjMat.indices[self.sp_AdjMat.indices[:,0]==action][:,1].numpy()
    nn_Js = np.where(self.sp_AdjMat.indices[:,0]==action)[0]
    nn_sum = 0
    for i in range(len(nns)): nn_sum += self.interaction[nn_Js[i]]*self._state[nns[i],0]
    reward = 2*nn_sum*self._state[action,0]
    return reward[0]

  def computeEnergy(self):
    edge = self.sp_AdjMat.indices.numpy()
    Nedge = len(edge)
    energy = 0
    for i in range(Nedge):
        energy -= self.interaction[i][0]*self._state[edge[i][0]][0]*self._state[edge[i][1]][0]
    return energy/2

  def _reset(self):
    self._state = np.ones(shape=(self.N,1)).astype("int32")
    #self.interaction = J_inter(self.dense_AdjMat)[0]    
    #self.inter_matrix = J_inter(self.dense_AdjMat)[1]
    self._episode_ended = False
    return ts.restart(np.array(self._state, dtype=np.int32))

  def _step(self, action):
    if self._episode_ended:
      return self.reset()

    if self.__all_spins_down():
      self._episode_ended = True
    elif (action>=0 and action<=self.N-1) and (self._state[action,0]==1):
      self._state[action,0]=-1
      rew = self.computeReward(action)
      
      if self.__all_spins_down():
          self._episode_ended = True
          return ts.termination(np.array(self._state, dtype=np.int32), reward=rew)
      else:
          return ts.transition(np.array(self._state, dtype=np.int32), reward=rew)
    
    elif (action>=0 and action<=self.N-1) and (self._state[action,0]==-1):
      return ts.transition(np.array(self._state, dtype=np.int32), reward=0)
    else:
      raise ValueError('`action` should be 0 up to N-1 - Spin Flip!')

## Dataset

In [8]:
class MyDataset(Dataset):
    def __init__(self, N_graph, X, Y, A, E, **kwargs):
        self.X = X
        self.Y = Y
        self.N_graph = N_graph
        self.A = A
        self.E = E
        super().__init__(**kwargs)

    def read(self):
        mydataset = []
        for i in range(self.N_graph):
            mydataset.append(
                    Graph(x=self.X[i], a=self.A[i], e=self.E[i], y=self.Y[i])      
                    )
        return mydataset

## Agent

In [9]:
def agent(N,                          # number nodes
          D,                          # number dimensions
          stack_channels=5,
          node_channels=3,
          edge_channels=3,
          division_factor_dense=4,
          p_drop=0,
          N_xenet=2,
          N_dense=2,
          activation="relu",
          regularizer=0,
          lr=0.001):
  inX = Input(shape=(N,1), name='Input Nodes')
  inA = Input(shape=(N,N), name='Input Adj matrix')
  inE = Input(shape=(N,N,1), name='Input Edges')
       
  X, E =  XENetDenseConv(stack_channels, node_channels, edge_channels,
                               attention=True, node_activation=activation, edge_activation=activation, 
                               kernel_regularizer=l2(regularizer), name="XENet_layer_0")([inX, inA, inE])
  for i in range(N_xenet-1):
    X, E =  XENetDenseConv(stack_channels, node_channels, edge_channels,
                               attention=True, node_activation=activation, edge_activation=activation, 
                               kernel_regularizer=l2(regularizer), name="XENet_layer_"+str(i+1))([X, inA, E])
  
  flat_x, flat_e = Flatten(name="Nodes_encoding")(X), Flatten(name="Edges_encoding")(E)
  out = Concatenate(axis=1, name="Concatenation")([flat_x])      # , flat_e   
  
  for i in range(N_dense):
    out = Dense(out.shape.as_list()[1]//division_factor_dense, activation=activation, kernel_regularizer=l2(regularizer))(out)
    out = Dropout(p_drop)(out)
  out = Dense(N, activation="PReLU", kernel_regularizer=l2(regularizer), name='Q-values')(out)
  
  model = Model([inX,inA,inE], out)
  model.compile(optimizer=Adam(lr), loss=MeanSquaredError())
  return model

## Training

In [10]:
def train(env, replay_memory, model, target_model, done, MIN_REPLAY_SIZE, batch_size, discount_factor):
 
    #print("\t=> replay_memory size:", len(replay_memory))
    if len(replay_memory) < MIN_REPLAY_SIZE:
        print("\t=> EXIT\n")
        return

    batch_size = batch_size
    mini_batch = random.sample(replay_memory, batch_size)

    E = np.array([transition[-1] for transition in mini_batch])
    A = np.array([transition[-2] for transition in mini_batch])
    current_states = np.array([transition[0] for transition in mini_batch])
    #current_qs_list = np.array([model.predict([current_states[new_current_states[i],A[i],E[i]])[0] for i in range(batch_size)])
    current_qs_list = np.array(model.predict([current_states,A,E]))
    #current_qs_list = model.predict(current_states[1])[0]

    new_current_states = np.array([transition[3] for transition in mini_batch])
    #future_qs_list = np.array([target_model.predict(new_current_states[i],A[i],E[i])[0] for i in range(batch_size)])
    future_qs_list = np.array(target_model.predict([new_current_states,A,E]))
    #future_qs_list = target_model.predict(new_current_states).numpy()[0]

    X = []
    Y = []
    for index, (observation, action, reward, new_observation, done, dense_AdjMat, inter_matrix) in enumerate(mini_batch):
        if not done:
            max_future_q = reward + discount_factor*np.max(future_qs_list[index])
            #max_future_q = sum of reward + discount_factor * np.max(future_qs_list[index])
        else:
            max_future_q = reward

        current_qs = current_qs_list[index]
        current_qs[action] = max_future_q

        
        X.append(observation)
        Y.append(current_qs)
    #print("\tX: ", np.array(X).shape, "\n", X)
    #print("\tY: ",np.array(Y).shape, "\n", Y)


    train_data = MyDataset(N_graph=batch_size, X=X, Y=Y, A=A, E=E)
    loader = BatchLoader(train_data, node_level=False, epochs=50, batch_size=batch_size, shuffle=False) 
    model.fit(loader.load(), steps_per_epoch=loader.steps_per_epoch, verbose=2, callbacks = [WandbCallback()])

In [11]:
def get_replay_memory(trajectory_buffer, replay_memory):
    n = len(trajectory_buffer)
    print("n =", n)

    states = np.array([transition[0] for transition in trajectory_buffer])
    actions = np.array([transition[1] for transition in trajectory_buffer])
    rewards = np.array([transition[2] for transition in trajectory_buffer])
    done = np.array([transition[4] for transition in trajectory_buffer])
    inter_matrix = trajectory_buffer[0][-1]
    dense_AdjMat = trajectory_buffer[0][-2]

    cum_reward = np.cumsum(rewards)

    replay_memory.append([states[0], actions[0], cum_reward[n-1], states[n-1], done[n-1], dense_AdjMat, inter_matrix])

    return replay_memory

## Main

In [12]:
def main(config=None):
    # set random seed for reproducibility
    RANDOM_SEED = 5
    tf.random.set_seed(RANDOM_SEED)
    np.random.seed(RANDOM_SEED)

    
    with wandb.init(config=config):
        config = wandb.config

        L = 5
        D = 2
        env = SG_env(L=L, D=D)

        epsilon = 1          # Epsilon-greedy algorithm in initialized at 1 meaning every step is random at the start
        max_epsilon = 1      # You can't explore more than 100% of the time
        min_epsilon = 0.01   # At a minimum, we'll always explore 1% of the time
        decay = config.decay

        # 1. Initialize the Target and Main models 
        # Main Model (updated every 4 steps)
        model = agent(N=env.N, D=D, stack_channels=config.stack_channels,
                      node_channels=config.node_channels, edge_channels=config.edge_channels,
                      N_xenet=config.N_xenet, N_dense=config.N_dense, 
                      division_factor_dense=config.division_factor_dense, p_drop=config.p_drop, lr=config.lr)

        # Target Model (updated at the end of every episode)
        target_model = agent(N=env.N, D=D, stack_channels=config.stack_channels,
                             node_channels=config.node_channels, edge_channels=config.edge_channels,
                             N_xenet=config.N_xenet, N_dense=config.N_dense, 
                             division_factor_dense=config.division_factor_dense, p_drop=config.p_drop, lr=config.lr)
        target_model.set_weights(model.get_weights())

        energy_buffer = []
        replay_memory = []
        
        # custom plot parameters
        ep_ene_min_data = []
        step_ene_min_data = []  
        
        train_episodes = config.train_episodes
        for episode in range(train_episodes):
            trajectory_buffer = []       
            ep_min_energy = np.inf
            total_training_rewards = 0
            steps_to_update_target_model = 0
            env.reset()
            previous_obs = np.ones(shape=(env.N,1)).astype("int32")
            done = False  
            check = np.arange(0,env.N)

            while not done: 
                observation = env.get_state()          
                print("\n\n\t\t\t\t++++++++++++  episode:", episode," - step:", steps_to_update_target_model, " ++++++++++++")

                # 2. Explore using the Epsilon Greedy Exploration Strategy
                random_number = np.random.rand()
                if random_number <= epsilon:
                    # Explore
                    action = random.choice(check)

                else:
                    # Exploit best known action
                    predicted = model([observation.reshape(1,env.N,1), env.dense_AdjMat.reshape(1,env.N,env.N), env.inter_matrix.reshape(1,env.N,env.N,1)], training=False).numpy()[0]
                    while True:
                        #check to prevent flipping the same spin twice - only once!
                        action = np.argmax(predicted)
                        if env.get_state()[action,0] == 1:
                                break;
                        predicted[action] = np.NINF

                check = np.setdiff1d(check, action)
                step_type, reward, discount, new_observation = env._step(action)
                done = env._episode_ended
                e = env.computeEnergy()
                trajectory_buffer.append([previous_obs, action, reward, new_observation, done, e, env.dense_AdjMat, env.inter_matrix])
                energy_buffer.append([episode, new_observation, env.interaction, e])
                if ep_min_energy>e: ep_min_energy = e
                
                # load interesting parameters to weight&Biases
                step_ene_min_data.append([e, episode*env.N+steps_to_update_target_model])  
                wandb.log({
                    #"Episode": energy_buffer[episode*env.N+steps_to_update_target_model][0],
                    #"Step": episode*env.N+steps_to_update_target_model,
                    "New observation": wandb.Image(energy_buffer[episode*env.N+steps_to_update_target_model][1].reshape(L,L)),
                    "J interactions": energy_buffer[episode*env.N+steps_to_update_target_model][2],
                    #"Energy": energy_buffer[episode*env.N+steps_to_update_target_model][3]
                })
    

                #if steps_to_update_target_model >= config.step_buffer:   
                if steps_to_update_target_model >= config.step_buffer and steps_to_update_target_model <= config.step_buffer+config.step_buffer_set:
                    replay_memory = get_replay_memory(trajectory_buffer, replay_memory)
                    trajectory_buffer = trajectory_buffer[1:]
                elif steps_to_update_target_model > config.step_buffer+config.step_buffer_set:       
                    trajectory_buffer = trajectory_buffer[1:]


                # 3. Update the Main Network using the Bellman Equation  
                #if (steps_to_update_target_model%L==0 and steps_to_update_target_model!=0) or done:
                print("\n\t\t\t\t\t      +++++ Training +++++")
                train(env, replay_memory, model, target_model, done, config.MIN_REPLAY_SIZE, config.batch_size, config.discount_factor)
    
                previous_obs = new_observation

        
                if done:
                    if episode%config.set_target==0:
                        #Copying main network weights to the target network weights
                        target_model.set_weights(model.get_weights())
                        
                steps_to_update_target_model += 1

            epsilon = min_epsilon + (max_epsilon - min_epsilon) * np.exp(-decay * episode) 
            ep_ene_min_data.append([ep_min_energy, episode]) 
        
        # load interesting parameters to weight&Biases
        wandb.log({
            "ep_ene_min_data" : wandb.Table(data=ep_ene_min_data, columns=["energy minima", "episode"]),
            "step_ene_min_data" : wandb.Table(data=step_ene_min_data, columns=["energy", "step"])
        }) 

In [ ]:
wandb.agent(sweep_id, main, count=10)

wandb: Agent Starting Run: lwqporba with config:
wandb: 	MIN_REPLAY_SIZE: 200
wandb: 	N_dense: 4
wandb: 	N_xenet: 2
wandb: 	batch_size: 115
wandb: 	decay: 0.01379563851782216
wandb: 	discount_factor: 0.2976773286680262
wandb: 	division_factor_dense: 1
wandb: 	edge_channels: 169
wandb: 	lr: 0.0060759129552070065
wandb: 	node_channels: 60
wandb: 	p_drop: 0
wandb: 	set_target: 6
wandb: 	stack_channels: 94
wandb: 	step_buffer: 8
wandb: 	step_buffer_set: 6
wandb: 	train_episodes: 145
wandb: Currently logged in as: filippo_festa (locp). Use `wandb login --relogin` to force relogin
2022-06-15 18:08:41.426171: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-06-15 18:08:41.426211: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/opt/conda/lib/python3.9/site-

2022-06-15 18:08:43.480581: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2022-06-15 18:08:43.480618: W tensorflow/stream_executor/cuda/cuda_driver.cc:269] failed call to cuInit: UNKNOWN ERROR (303)
2022-06-15 18:08:43.480636: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (1fc8dd2abdfa): /proc/driver/nvidia/version does not exist
2022-06-15 18:08:43.481021: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.




				++++++++++++  episode: 0  - step: 0  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 1  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 2  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 3  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 4  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 5  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 6  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 7  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 8  ++++++++++++
n = 9

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 0  - step: 9  ++++++++++++
n = 9

					      +++++ Training +++++
	=> EXIT

/opt/conda/lib/python3.9/site-packages/wandb/sdk/data_types/image.py:439: RuntimeWarning: invalid value encountered in true_divide
  data = (data - np.min(data)) / np.ptp(data)




				++++++++++++  episode: 1  - step: 0  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 1  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 2  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 3  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 4  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 5  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 6  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 7  ++++++++++++

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 8  ++++++++++++
n = 9

					      +++++ Training +++++
	=> EXIT



				++++++++++++  episode: 1  - step: 9  ++++++++++++
n = 9

					      +++++ Training +++++
	=> EXIT

...

1/1 - 2s - loss: 0.1784 - _timestamp: 1655333890.0000 - _runtime: 4940.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 94  - step: 7  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2424 - _timestamp: 1655333892.0000 - _runtime: 4942.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 94  - step: 8  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.2117 - _timestamp: 1655333895.0000 - _runtime: 4945.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 94  - step: 9  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.1771 - _timestamp: 1655333897.0000 - _runtime: 4947.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 94  - step: 10  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.1538 - _timestamp: 1655333900.0000 - _runtime: 4950.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 94  - step: 11  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.1658 - _timestamp: 1



				++++++++++++  episode: 96  - step: 0  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.1544 - _timestamp: 1655334012.0000 - _runtime: 5062.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 96  - step: 1  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2987 - _timestamp: 1655334015.0000 - _runtime: 5065.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 96  - step: 2  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2244 - _timestamp: 1655334017.0000 - _runtime: 5067.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 96  - step: 3  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2415 - _timestamp: 1655334020.0000 - _runtime: 5070.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 96  - step: 4  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.1841 - _timestamp: 1655334022.0000 - _runtime: 5072.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 96  - step: 5  ++++++++++++

					  

1/1 - 2s - loss: 0.1617 - _timestamp: 1655334131.0000 - _runtime: 5181.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 97  - step: 19  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.3205 - _timestamp: 1655334134.0000 - _runtime: 5184.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 97  - step: 20  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.1738 - _timestamp: 1655334137.0000 - _runtime: 5187.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 97  - step: 21  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2076 - _timestamp: 1655334140.0000 - _runtime: 5190.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 97  - step: 22  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2628 - _timestamp: 1655334143.0000 - _runtime: 5193.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 97  - step: 23  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2885 - _timestamp: 1655334146.0000 - _run



				++++++++++++  episode: 99  - step: 12  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.3463 - _timestamp: 1655334250.0000 - _runtime: 5300.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 99  - step: 13  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.2613 - _timestamp: 1655334253.0000 - _runtime: 5303.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 99  - step: 14  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.3473 - _timestamp: 1655334256.0000 - _runtime: 5306.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 99  - step: 15  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.2909 - _timestamp: 1655334259.0000 - _runtime: 5309.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 99  - step: 16  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2560 - _timestamp: 1655334262.0000 - _runtime: 5312.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 99  - s

1/1 - 2s - loss: 0.2176 - _timestamp: 1655334371.0000 - _runtime: 5421.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 101  - step: 6  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2855 - _timestamp: 1655334373.0000 - _runtime: 5423.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 101  - step: 7  ++++++++++++

					      +++++ Training +++++
1/1 - 2s - loss: 0.2054 - _timestamp: 1655334376.0000 - _runtime: 5426.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 101  - step: 8  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.1737 - _timestamp: 1655334379.0000 - _runtime: 5429.0000 - 2s/epoch - 2s/step


				++++++++++++  episode: 101  - step: 9  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 3s - loss: 0.1620 - _timestamp: 1655334382.0000 - _runtime: 5432.0000 - 3s/epoch - 3s/step


				++++++++++++  episode: 101  - step: 10  ++++++++++++
n = 9

					      +++++ Training +++++
1/1 - 2s - loss: 0.2744 - _timestamp: 165

In [ ]:
wandb.finish()